In [1]:
# from ElementType import *
# from NewElementTypeSet import *
from py2neo import *
from Schema import *
from neo4j import GraphDatabase
from pickle5 import pickle
import matplotlib.pyplot as plt
from sklearn.feature_extraction.text import CountVectorizer
import plotly.graph_objects as go
from sklearn.manifold import TSNE
import numpy as np
import re
import json
import pydot
sc = Schema()
# sc = pickle.load(open('schema_snb-1_all_nodes_rels.pickle','rb',-1))
# sc = pickle.load(open('stored_schema/snb_schema_emailLanguage_modifiedEdgeTypeSet','rb',-1))
sc_new = pickle.load(open('sc_with_edges.pkl','rb',-1))
# sc = pickle.load(open('schema_snb-1_all_nodes_rels_withEmailLanguage.pickle', 'rb',-1))
snb_gt_sc = pickle.load(open('stored_schema/schema_snb-1_all_nodes_rels_ground_truth.pickle','rb',-1))
# cpg_sc = pickle.load(open('stored_schema/cpg_3files_sc.pkl','rb',-1))
# gt_cpg_sc = pickle.load(open('stored_schema/gt_cpg_sc_stl_enhanced.pkl','rb',-1))

# graph = Graph('bolt://localhost:11006',name='shop',password='shop')
# graph = Graph('bolt://localhost:11003',name='neo4j')
# sc = pickle.load(open('schema_snb-1_all_nodes_rels.pickle','rb',-1))
# graph = Graph('bolt://localhost:7687',name='mb6',password='mb6')
# graph = Graph('bolt://localhost:11003',name='social')
# # graph = Graph('bolt://localhost:7687',name='gmark')
# import pickle
# mb6_sc = pickle.load(open('stored_schema/schema_mb6_allNodesRels.pickle','rb',-1))
# mb6_gt_sc = pickle.load(open('stored_schema/schema_mb6_ground_truth.pickle','rb',-1))

In [7]:
cursor = graph.run('''
match (n)
with n, ((n)-->()) as out, (()-->(n)) as inc, rand() as ra
order by ra
return n, inc, out 
limit 30000
''')

In [8]:
sc_new = Schema()
sc_new.extractSchema(cursor=cursor,IGNORE_LABEL=True)

30000it [34:29, 14.50it/s]

Schema extraction time 2069.8224952220917


In [4]:
sc_new = Schema()
sc_new.extractSchema(cursor=cursor,IGNORE_LABEL=False)

EOFError: Ran out of input

In [7]:
with open('snb_gt_topological.pkl','wb') as f:
    pickle.dump(snb_gt_sc,f,-1)

In [8]:
# for et in sc_new.edgetypeset.edgetypes:
#     et.src_type.removeLabelsFromAttr()
#     et.target_type.removeLabelsFromAttr()
# sc_new.edgetypeset.print()

In [21]:
et.src_type.removeLabelsFromAttr()
et.src_type.print()

------------Content Type----------------
name?    str            
id?      int            
url?     str            
TagClass? LBL            


In [11]:
# nt = sc_new.node_types[0]
# nt.removeLabelsFromAttr()
snb_gt_sc.edgetypeset.print()

number of edge types  20
index  0
source
------------Content Type----------------
creationDate? int            
title?   str            
id?      int            
edge
------------Content Type----------------
CONTAINER_OF? LBL            
target
------------Content Type----------------
creationDate? int            
browserUsed? str            
locationIP? str            
content? str            
length?  int            
language? str            
imageFile? str            
id?      int            
index  1
source
------------Content Type----------------
creationDate? int            
browserUsed? str            
locationIP? str            
content? str            
length?  int            
id?      int            
edge
------------Content Type----------------
HAS_CREATOR? LBL            
target
------------Content Type----------------
creationDate? int            
firstName? str            
lastName? str            
gender?  str            
birthday? int            
email?   list          

In [3]:
# import pickle5 as pickle
# with open('snb_withedges_3w.pkl','wb') as f:
#     pickle.dump(sc_new, f)
# sc_new.print()

In [36]:
for e in sc_new.node_types[26].outgoing_edges:
    e.print()
# sc_new.node_types[7]

------------Content Type----------------
IS_PART_OF? LBL            


In [18]:
city = NodeType(attr_type={'name':set([str]), 'url':set([str])})
city.incoming_edges.add(ContentType(elem={'IS_LOCATED_IN':LBL()}))
list(city.incoming_edges)[0].print()

------------Content Type----------------
IS_LOCATED_IN? LBL            


In [4]:
# import pickle5 as pickle
# with open('sc_with_edges.pkl','wb') as f:
#     pickle.dump(sc_new,f)

In [44]:
import graphsim as gs
# help(gs.tacsim_combined)
# gs.tacsim_in_C(g)
preds = nx.jaccard_coefficient(g)
for u, v, p in preds:
    if p>0.5:
        print('(%d, %d) -> %.8f' % (u, v, p))

(3, 22) -> 0.53333333
(4, 12) -> 0.53333333
(6, 17) -> 0.52631579
(8, 26) -> 0.66666667


In [45]:
gt_cpg_sc.nodetypeset.nodetypes[3].print()
gt_cpg_sc.nodetypeset.nodetypes[22].print()
# gt_cpg_sc.nodetypeset.nodetypes[3].print()

------------Content Type----------------
code?    str            
order?   int            
name?    str            
typeFullName? str            
lineNumber? int            
columnNumber? int            
evaluationStrategy? str            
dynamicTypeHintFullName? str            
METHOD_PARAMETER_IN? LBL            
id?      int            
------------Content Type----------------
code?    str            
order?   int            
argumentIndex? int            
typeFullName? str            
lineNumber? int            
columnNumber? int            
dynamicTypeHintFullName? str            
TYPE_REF? LBL            
id?      int            


In [19]:
sim = nx.simrank_similarity(g)
lol = [[sim[u][v] for v in sorted(sim[u])] for u in sorted(sim)]
sim_array = np.array(lol)

In [20]:
for i in range(len(sim_array)):
    for j in range(i+1, len(sim_array)):
        if sim_array[i,j]>0.5:
            print(i,j,sim_array[i,j])

1 2 0.7421602787456445
1 3 0.7212543554006967
2 3 0.7421602787456445


In [2]:
from pickle5 import pickle
cpg_sc = pickle.load(open('stl_cpg_schema.pkl','rb',-1))
gt_cpg_sc = pickle.load(open('gt_cpg_sc_stl_enhanced.pkl','rb',-1))
cpg_sc.mergeBySimAndEdge(comb='AND')
cpg_sc.nodetypeset.print()

source
------------Content Type----------------
name?    str            
astParentFullName? str            
columnNumberEnd? int            
fullName? str            
signature? str            
astParentType? str            
columnNumber? int            
lineNumberEnd? int            
code?    str            
isExternal? bool           
lineNumber? int            
id?      int            
order?   int            
filename? str            
METHOD?  LBL            
edge
------------Content Type----------------
DDG?     LBL            
target
------------Content Type----------------
dynamicTypeHintFullName? list           
name?    str            
evaluationStrategy? str            
code?    str            
typeFullName? str            
columnNumber? int            
order?   int            
lineNumber? int            
id?      int            
METHOD_PARAMETER_IN? LBL            
source
------------Content Type----------------
dynamicTypeHintFullName? list           
name?    str          

DDG?     LBL            
target
------------Content Type----------------
dynamicTypeHintFullName? list           
evaluationStrategy? str            
code?    str            
typeFullName? str            
columnNumber? int            
order?   int            
lineNumber? int            
id?      int            
METHOD_RETURN? LBL            
source
------------Content Type----------------
name?    str            
astParentFullName? str            
columnNumberEnd? int            
fullName? str            
signature? str            
astParentType? str            
columnNumber? int            
lineNumberEnd? int            
code?    str            
isExternal? bool           
lineNumber? int            
id?      int            
order?   int            
filename? str            
METHOD?  LBL            
edge
------------Content Type----------------
DDG?     LBL            
target
------------Content Type----------------
code?    str            
columnNumber? int            
order?   int  

parserTypeName? str            
code?    str            
columnNumber? int            
order?   int            
controlStructureType? str            
argumentIndex? int            
lineNumber? int            
id?      int            
CONTROL_STRUCTURE? LBL            
resi, resj similarity 0.5401002506265664
source
------------Content Type----------------
name?    str            
astParentFullName? str            
columnNumberEnd? int            
fullName? str            
signature? str            
astParentType? str            
columnNumber? int            
lineNumberEnd? int            
code?    str            
isExternal? bool           
lineNumber? int            
id?      int            
order?   int            
filename? str            
METHOD?  LBL            
edge
------------Content Type----------------
AST?     LBL            
target
------------Content Type----------------
dynamicTypeHintFullName? list           
name?    str            
evaluationStrategy? str            
c

lineNumberEnd? int            
code?    str            
isExternal? bool           
lineNumber? int            
id?      int            
order?   int            
filename? str            
METHOD?  LBL            
edge
------------Content Type----------------
AST?     LBL            
target
------------Content Type----------------
dynamicTypeHintFullName? list           
code?    str            
typeFullName? str            
columnNumber? int            
order?   int            
argumentIndex? int            
lineNumber? int            
id?      int            
BLOCK?   LBL            
source
------------Content Type----------------
dynamicTypeHintFullName? list           
code?    str            
typeFullName? str            
columnNumber? int            
order?   int            
argumentIndex? int            
lineNumber? int            
id?      int            
BLOCK?   LBL            
edge
------------Content Type----------------
AST?     LBL            
target
------------Content Ty

code?    str            
typeFullName? str            
order?   int            
argumentIndex? int            
id?      int            
BLOCK?   LBL            
source
------------Content Type----------------
dynamicTypeHintFullName? list           
code?    str            
typeFullName? str            
columnNumber? int            
order?   int            
argumentIndex? int            
lineNumber? int            
id?      int            
BLOCK?   LBL            
edge
------------Content Type----------------
AST?     LBL            
target
------------Content Type----------------
parserTypeName? str            
code?    str            
columnNumber? int            
order?   int            
controlStructureType? str            
argumentIndex? int            
lineNumber? int            
id?      int            
CONTROL_STRUCTURE? LBL            
resi, resj similarity 0.5321637426900584
source
------------Content Type----------------
name?    str            
astParentFullName? str       

...

argumentIndex? int            
dynamicTypeHintFullName? list           
dispatchType? str            
signature? str            
lineNumber? int            
id?      int            
CALL?    LBL            
edge
------------Content Type----------------
AST?     LBL            
target
------------Content Type----------------
dynamicTypeHintFullName? list           
parserTypeName? str            
code?    str            
typeFullName? str            
columnNumber? int            
order?   int            
argumentIndex? int            
lineNumber? int            
id?      int            
UNKNOWN? LBL            
source
------------Content Type----------------
name?    str            
astParentFullName? str            
fullName? str            
signature? str            
astParentType? str            
code?    str            
isExternal? bool           
id?      int            
order?   int            
filename? str            
METHOD?  LBL            
edge
------------Content Type-------

target
------------Content Type----------------
dynamicTypeHintFullName? list           
parserTypeName? str            
code?    str            
typeFullName? str            
columnNumber? int            
order?   int            
argumentIndex? int            
lineNumber? int            
id?      int            
UNKNOWN? LBL            
resi, resj similarity 0.5599415204678363
source
------------Content Type----------------
name?    str            
astParentFullName? str            
columnNumberEnd? int            
fullName? str            
signature? str            
astParentType? str            
columnNumber? int            
lineNumberEnd? int            
code?    str            
isExternal? bool           
lineNumber? int            
id?      int            
order?   int            
filename? str            
METHOD?  LBL            
edge
------------Content Type----------------
AST?     LBL            
target
------------Content Type----------------
dynamicTypeHintFullName? list   

code?    str            
columnNumber? int            
order?   int            
argumentIndex? int            
lineNumber? int            
id?      int            
RETURN?  LBL            
edge
------------Content Type----------------
DDG?     LBL            
target
------------Content Type----------------
dynamicTypeHintFullName? list           
evaluationStrategy? str            
code?    str            
typeFullName? str            
columnNumber? int            
order?   int            
lineNumber? int            
id?      int            
METHOD_RETURN? LBL            
resi, resj similarity 0.5818181818181818
source
------------Content Type----------------
name?    str            
astParentFullName? str            
fullName? str            
signature? str            
astParentType? str            
code?    str            
isExternal? bool           
id?      int            
order?   int            
filename? str            
METHOD?  LBL            
edge
------------Content Type-----

lineNumber? int            
id?      int            
CONTROL_STRUCTURE? LBL            
edge
------------Content Type----------------
AST?     LBL            
target
------------Content Type----------------
dynamicTypeHintFullName? list           
parserTypeName? str            
code?    str            
typeFullName? str            
order?   int            
argumentIndex? int            
id?      int            
UNKNOWN? LBL            
source
------------Content Type----------------
name?    str            
astParentFullName? str            
columnNumberEnd? int            
fullName? str            
signature? str            
astParentType? str            
columnNumber? int            
lineNumberEnd? int            
code?    str            
isExternal? bool           
lineNumber? int            
id?      int            
order?   int            
filename? str            
METHOD?  LBL            
edge
------------Content Type----------------
AST?     LBL            
target
------------C

astParentFullName? str            
fullName? str            
signature? str            
astParentType? str            
code?    str            
isExternal? bool           
id?      int            
order?   int            
filename? str            
METHOD?  LBL            
edge
------------Content Type----------------
DDG?     LBL            
target
------------Content Type----------------
dynamicTypeHintFullName? list           
name?    str            
evaluationStrategy? str            
code?    str            
typeFullName? str            
order?   int            
id?      int            
METHOD_PARAMETER_IN? LBL            
source
------------Content Type----------------
name?    str            
astParentFullName? str            
fullName? str            
signature? str            
astParentType? str            
code?    str            
isExternal? bool           
id?      int            
order?   int            
filename? str            
METHOD?  LBL            
edge
------------C

In [109]:
cpg_sc.computeF1score(gt_cpg_sc,igoreDatatype=True)

7 25 9
precision:  0.4375
recall:  0.21875
f1_score:  0.2916666666666667
7 371 23
precision:  0.23333333333333334
recall:  0.018518518518518517
f1_score:  0.03431372549019607


In [3]:
# sc.mergeByJaccardSim(idf=True)
from pickle5 import pickle
sc = pickle.load(open('snb_schema_emailLanguage_modifiedEdgeTypeSet','rb',-1))
sc.mergeBySimAndEdge(comb='AND')
# sc.nodetypeset.print()

source
------------Content Type----------------
name?    str            
id?      int            
url?     str            
Company? LBL            
Organisation? LBL            
edge
------------Content Type----------------
IS_LOCATED_IN? LBL            
target
------------Content Type----------------
name?    str            
id?      int            
url?     str            
Country? LBL            
Place?   LBL            
source
------------Content Type----------------
browserUsed? str            
length?  int            
locationIP? str            
id?      int            
creationDate? int            
content? str            
Comment? LBL            
Message? LBL            
edge
------------Content Type----------------
IS_LOCATED_IN? LBL            
target
------------Content Type----------------
name?    str            
id?      int            
url?     str            
Country? LBL            
Place?   LBL            
resi, resj similarity 0.6944444444444443
source
------------Co

Country? LBL            
Place?   LBL            
resi, resj similarity 0.6944444444444443
source
------------Content Type----------------
name?    str            
id?      int            
url?     str            
Company? LBL            
Organisation? LBL            
edge
------------Content Type----------------
IS_LOCATED_IN? LBL            
target
------------Content Type----------------
name?    str            
id?      int            
url?     str            
Country? LBL            
Place?   LBL            
source
------------Content Type----------------
birthday? int            
firstName? str            
lastName? str            
gender?  str            
browserUsed? str            
locationIP? str            
id?      int            
creationDate? int            
Person?  LBL            
email?   list           
speaks?  list           
edge
------------Content Type----------------
IS_LOCATED_IN? LBL            
target
------------Content Type----------------
name?    str     

browserUsed? str            
length?  int            
locationIP? str            
id?      int            
creationDate? int            
content? str            
Comment? LBL            
Message? LBL            
edge
------------Content Type----------------
HAS_CREATOR? LBL            
target
------------Content Type----------------
birthday? int            
firstName? str            
lastName? str            
gender?  str            
browserUsed? str            
locationIP? str            
id?      int            
creationDate? int            
Person?  LBL            
email?   list           
speaks?  list           
resi, resj similarity 0.9
source
------------Content Type----------------
browserUsed? str            
length?  int            
locationIP? str            
language? str            
id?      int            
creationDate? int            
content? str            
Message? LBL            
Post?    LBL            
edge
------------Content Type----------------
HAS_TAG? LBL    

lastName? str            
gender?  str            
browserUsed? str            
locationIP? str            
id?      int            
creationDate? int            
Person?  LBL            
email?   list           
speaks?  list           
source
------------Content Type----------------
browserUsed? str            
length?  int            
locationIP? str            
id?      int            
creationDate? int            
content? str            
Comment? LBL            
Message? LBL            
edge
------------Content Type----------------
HAS_CREATOR? LBL            
target
------------Content Type----------------
birthday? int            
firstName? str            
lastName? str            
gender?  str            
browserUsed? str            
locationIP? str            
id?      int            
creationDate? int            
Person?  LBL            
email?   list           
speaks?  list           
resi, resj similarity 0.8666666666666667
source
------------Content Type----------------

locationIP? str            
language? str            
id?      int            
creationDate? int            
content? str            
Message? LBL            
Post?    LBL            
edge
------------Content Type----------------
IS_LOCATED_IN? LBL            
target
------------Content Type----------------
name?    str            
id?      int            
url?     str            
Country? LBL            
Place?   LBL            
resi, resj similarity 0.5811965811965812
source
------------Content Type----------------
browserUsed? str            
length?  int            
locationIP? str            
language? str            
id?      int            
creationDate? int            
content? str            
Message? LBL            
Post?    LBL            
edge
------------Content Type----------------
IS_LOCATED_IN? LBL            
target
------------Content Type----------------
name?    str            
id?      int            
url?     str            
Country? LBL            
Place?   LBL  

length?  int            
locationIP? str            
language? str            
id?      int            
creationDate? int            
content? str            
Message? LBL            
Post?    LBL            
edge
------------Content Type----------------
IS_LOCATED_IN? LBL            
target
------------Content Type----------------
name?    str            
id?      int            
url?     str            
Country? LBL            
Place?   LBL            
resi, resj similarity 0.9
source
------------Content Type----------------
imageFile? str            
browserUsed? str            
length?  int            
locationIP? str            
id?      int            
creationDate? int            
Message? LBL            
Post?    LBL            
edge
------------Content Type----------------
HAS_CREATOR? LBL            
target
------------Content Type----------------
birthday? int            
firstName? str            
lastName? str            
gender?  str            
browserUsed? str          

firstName? str            
lastName? str            
gender?  str            
browserUsed? str            
locationIP? str            
id?      int            
creationDate? int            
Person?  LBL            
email?   list           
speaks?  list           
edge
------------Content Type----------------
IS_LOCATED_IN? LBL            
target
------------Content Type----------------
name?    str            
id?      int            
url?     str            
City?    LBL            
Place?   LBL            
source
------------Content Type----------------
browserUsed? str            
length?  int            
locationIP? str            
language? str            
id?      int            
creationDate? int            
content? str            
Message? LBL            
Post?    LBL            
edge
------------Content Type----------------
IS_LOCATED_IN? LBL            
target
------------Content Type----------------
name?    str            
id?      int            
url?     str            

id?      int            
url?     str            
Country? LBL            
Place?   LBL            
resi, resj similarity 0.7777777777777777
source
------------Content Type----------------
name?    str            
id?      int            
url?     str            
City?    LBL            
Place?   LBL            
edge
------------Content Type----------------
IS_PART_OF? LBL            
target
------------Content Type----------------
name?    str            
id?      int            
url?     str            
Country? LBL            
Place?   LBL            
source
------------Content Type----------------
name?    str            
id?      int            
url?     str            
Country? LBL            
Place?   LBL            
edge
------------Content Type----------------
IS_PART_OF? LBL            
target
------------Content Type----------------
name?    str            
id?      int            
url?     str            
Continent? LBL            
Place?   LBL            
resi, resj simila

edge
------------Content Type----------------
IS_LOCATED_IN? LBL            
target
------------Content Type----------------
name?    str            
id?      int            
url?     str            
City?    LBL            
Place?   LBL            
source
------------Content Type----------------
imageFile? str            
browserUsed? str            
length?  int            
locationIP? str            
id?      int            
creationDate? int            
Message? LBL            
Post?    LBL            
edge
------------Content Type----------------
IS_LOCATED_IN? LBL            
target
------------Content Type----------------
name?    str            
id?      int            
url?     str            
Country? LBL            
Place?   LBL            
resi, resj similarity 0.5833333333333334
source
------------Content Type----------------
name?    str            
id?      int            
url?     str            
Organisation? LBL            
University? LBL            
edge
-----------

In [4]:
sc.computeF1score(snb_gt_sc)

5 9 3
precision:  0.625
recall:  0.35714285714285715
f1_score:  0.45454545454545453
13 7 6
precision:  0.6842105263157895
recall:  0.65
f1_score:  0.6666666666666667


In [4]:
sc.print()

semantic:  at_least_one_match
node type
number of node types  8
number of elements:  1575
------------Content Type----------------
name     str            
id       int            
url      str            
Company? LBL            
Organisation LBL            
University? LBL            
number of elements:  151043
------------Content Type----------------
browserUsed str            
length   int            
locationIP str            
id       int            
creationDate int            
content? str            
Comment? LBL            
Message  LBL            
language? str            
Post?    LBL            
imageFile? str            
number of elements:  6380
------------Content Type----------------
name?    str            
id?      int            
url?     str            
Tag?     LBL            
number of elements:  16080
------------Content Type----------------
name?    str            
id?      int            
url?     str            
TagClass? LBL            
number of elements: 

In [5]:
org_sc = Schema()
org_sc.extractSchema(graph=graph)

  0%|          | 0/199 [00:00<?, ?it/s]

none node:  0


100%|██████████| 199/199 [00:10<00:00, 18.11it/s]

none relation:  0
Schema extraction time 17.302233457565308


In [7]:
org_sc.mergeByLabelsSet()
org_sc.print()

semantic:  at_least_one_match
node type
number of node types  12
number of elements:  1
------------Content Type----------------
_classLabel str            
_handleRDFTypes int            
_subClassOfRel str            
_handleMultival int            
_objectPropertyLabel str            
_rangeRel str            
_domainRel str            
_keepLangTag bool           
_subPropertyOfRell str            
_keepCustomDataTypes bool           
_handleVocabUris int            
_applyNeo4jNaming bool           
_dataTypePropertyLabel str            
_GraphConfig LBL            
number of elements:  29
------------Content Type----------------
uri      str            
Resource LBL            
name?    str            
mbox?    str            
number of elements:  9
------------Content Type----------------
comment? str            
label?   str            
uri      str            
Class    LBL            
Resource LBL            
number of elements:  1
------------Content Type----------------
uri 

target
------------Content Type----------------
uri?     str            
Resource? LBL            
source
------------Content Type----------------
comment? str            
label?   str            
uri?     str            
prefLabel? str            
Resource? LBL            
Role?    LBL            
edge
------------Content Type----------------
roleProperty? LBL            
target
------------Content Type----------------
comment? str            
label?   str            
uri?     str            
ObjectProperty? LBL            
Property? LBL            
Resource? LBL            
source
------------Content Type----------------
created? Date           
modified? Date           
comment? str            
versionInfo? str            
label?   str            
title?   str            
uri?     str            
Ontology? LBL            
Resource? LBL            
edge
------------Content Type----------------
seeAlso? LBL            
target
------------Content Type----------------
uri?     str      

In [2]:
edge_cursor = graph.run('match ()-[r]->() return r')
node_cursor = graph.run('match (n) return n')

In [3]:
cpg_sc = Schema()
cpg_sc.extractSchema(node_cursor=node_cursor, edge_cursor=edge_cursor)

15312it [00:06, 2324.16it/s]
38377it [08:59, 71.08it/s] 

Schema extraction time 546.5734341144562


In [2]:
mb6_sc.nodetypeset.nodetypes[10].print(), mb6_sc.nodetypeset.nodetypes[41].print()
sm, tm = mb6_sc.getNodeEdgeMap()
sm[mb6_sc.nodetypeset.nodetypes[10].toHashStr()], sm[mb6_sc.nodetypeset.nodetypes[41].toHashStr()]

------------Content Type----------------
roiInfo? str            
pre?     int            
post?    int            
size?    int            
bodyId?  int            
statusLabel? str            
status?  str            
Neuron?  LBL            
Segment? LBL            
mushroombody_Neuron? LBL            
mushroombody_Segment? LBL            
------------Content Type----------------
roiInfo? str            
pre?     int            
instance? str            
type?    str            
statusLabel? str            
post?    int            
size?    int            
alpha2?  bool           
bodyId?  int            
cropped? bool           
status?  str            
alpha1?  bool           
Neuron?  LBL            
Segment? LBL            
mushroombody_Neuron? LBL            
mushroombody_Segment? LBL            


([<ElementType.EdgeType at 0xe17cf70>,
 [<ElementType.EdgeType at 0xe2d0650>])

In [17]:
# com = min(np.array(src) , np.array(tar)) 
for i in range(len(src)):
    for j in range(i+1,len(src)):
        if min(src[i][j],tar[i][j])>0.5:
            print(i,j)
#         if com[i,j]>=0.5:
#             print(i,j)

2 3
2 4
2 5
2 6
2 7
2 8
2 9
2 11
2 12
2 13
2 15
2 17
2 18
2 19
2 20
2 21
2 22
2 23
2 25
2 26
2 27
2 28
2 30
2 31
2 32
2 33
2 35
2 38
2 39
2 40
2 43
2 44
2 46
2 47
2 48
3 4
3 5
3 6
3 7
3 8
3 9
3 11
3 12
3 13
3 15
3 17
3 18
3 19
3 20
3 21
3 22
3 23
3 25
3 26
3 27
3 28
3 30
3 31
3 32
3 33
3 35
3 38
3 39
3 40
3 43
3 44
3 46
3 47
3 48
4 5
4 6
4 7
4 8
4 9
4 11
4 12
4 13
4 15
4 17
4 18
4 19
4 20
4 21
4 22
4 23
4 25
4 26
4 27
4 28
4 30
4 31
4 32
4 33
4 35
4 38
4 39
4 40
4 43
4 44
4 46
4 47
4 48
5 6
5 7
5 8
5 9
5 11
5 12
5 13
5 15
5 17
5 18
5 19
5 20
5 21
5 22
5 23
5 25
5 26
5 27
5 28
5 30
5 31
5 32
5 33
5 35
5 38
5 39
5 40
5 43
5 44
5 46
5 47
5 48
6 7
6 8
6 9
6 11
6 12
6 13
6 15
6 17
6 18
6 19
6 20
6 21
6 22
6 23
6 25
6 26
6 27
6 28
6 30
6 31
6 32
6 33
6 35
6 38
6 39
6 40
6 43
6 44
6 46
6 47
6 48
7 8
7 9
7 11
7 12
7 13
7 15
7 17
7 18
7 19
7 20
7 21
7 22
7 23
7 25
7 26
7 27
7 28
7 30
7 31
7 32
7 33
7 35
7 38
7 39
7 40
7 43
7 44
7 46
7 47
7 48
8 9
8 11
8 12
8 13
8 15
8 17
8 18
8 19
8 20
8 21
8 2

In [14]:
sc.nodetypeset.nodetypes[7].print(),sc.nodetypeset.nodetypes[8].print()
# mb6_sc.nodetypeset.nodetypes[1].print(),mb6_sc.nodetypeset.nodetypes[14].print()

------------Content Type----------------
name?    str            
id?      int            
url?     str            
Country? LBL            
Place?   LBL            
------------Content Type----------------
name?    str            
id?      int            
url?     str            
City?    LBL            
Place?   LBL            


(None, None)

In [8]:
m = sc.getNodeEdgeMap()
m[sc.nodetypeset.nodetypes[2].toHashStr()]

In [6]:
edge_cursor = graph.run('match ()-[r]->() return r')
node_cursor = graph.run('match (n) return n')
sc = Schema()
sc.extractSchema(node_cursor=node_cursor, edge_cursor=edge_cursor)

In [6]:
with open('snb_schema_emailLanguage_modifiedEdgeTypeSet','wb') as f:
    pickle.dump(sc, f, -1)

In [24]:
subg  = graph.run('match (n:Person) where exists(n.speaks) AND exists(n.email) return n').to_subgraph()
sc.updateSchema(subg, UPDATE_REL=False, created_attr=set(['email','speaks']))
# sc.nodetypeset.print()

100%|██████████| 1528/1528 [00:00<00:00, 10928.31it/s]

updating type, type does not exist, creating type
remove  1  element


In [26]:
# with open('schema_snb-1_all_nodes_rels_withEmailLanguage.pickle', 'wb') as f:
#     pickle.dump(sc,f,-1)

In [11]:
# sc = pickle.load(open('schema_snb-1_all_nodes_rels.pickle','rb',-1))
# sc.extractSchema(graph=graph,sample_size=2000)
# with open('schema_mb6_allNodesRels_2_accurateNumOfElem.pickle', 'wb') as f:
#     pickle.dump(sc, f, -1)

In [4]:
sc.isConform(graph=graph)

  0%|          | 5/1477965 [00:00<8:42:13, 47.17it/s]

none node:  876


100%|██████████| 1477965/1477965 [6:37:29<00:00, 61.97it/s]   

none relation:  179
execution time:  -26750.547184944153


True

In [2]:
# subg = graph.run('MATCH (n) where rand() <= 0.0003 OPTIONAL MATCH (n)-[r]-() return *').to_subgraph()
# len(subg.relationships),len(subg.nodes)

In [16]:
sc.nodetypeset.mergeByJaccardSim()
sc.nodetypeset.print()

6 clusters found out of 11 nodes
number of node types  6
number of elements:  227
{'id': 'int', 'title': 'str', 'creationDate': 'int', 'Forum': 'LBL'}
number of elements:  208
{'browserUsed': 'str', 'length': 'int', 'locationIP': 'str', 'id': 'int', 'creationDate': 'int', 'content': 'str', 'Comment': 'LBL', 'Message': 'LBL', 'language': 'str', 'Post': 'LBL', 'imageFile': 'str'}
number of elements:  157
{'name': 'str', 'id': 'int', 'url': 'str', 'Tag': 'LBL', 'TagClass': 'LBL'}
number of elements:  50
{'birthday': 'int', 'firstName': 'str', 'lastName': 'str', 'gender': 'str', 'browserUsed': 'str', 'locationIP': 'str', 'id': 'int', 'creationDate': 'int', 'Person': 'LBL'}
number of elements:  169
{'name': 'str', 'id': 'int', 'url': 'str', 'Country': 'LBL', 'Place': 'LBL', 'City': 'LBL'}
number of elements:  149
{'name': 'str', 'id': 'int', 'url': 'str', 'Organisation': 'LBL', 'University': 'LBL', 'Company': 'LBL'}


In [5]:

with open('schema_social_allNodesRels.pickle', 'wb') as f:
    pickle.dump(sc, f, -1)

# sc.print()
# sc.nodetypeset.numOfType, sum(sc.nodetypeset.numOfType)

In [20]:
fsc = pickle.load(open('schema_snb-1_all_nodes_rels.pickle','rb',-1))
# import pickle
# mb_sc = pickle.load(open('schema_mb6_allNodesRels.pickle','rb',-1))

In [14]:
mb_sc.mergeByJaccardSim()
len(mb_sc.nodetypeset), len(mb_sc.edgetypeset)

4 clusters found out of 52 nodes
5 clusters found out of 461 nodes


(4, 5)

In [4]:
fsc.mergeByJaccardSim()
len(fsc.nodetypeset), len(fsc.edgetypeset)

6 clusters found out of 12 nodes
18 clusters found out of 29 nodes


(6, 18)